In [1]:
!pip install --upgrade pip
!pip install jiwer
!pip install evaluate
!pip install tensorboard
!pip install datasets
!pip install transformers
!pip install torch

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.8/1.8 MB 44.3 MB/s eta 0:00:0000:01
  Attempting uninstall: pip
    Found existing installation: pip 24.0
    Uninstalling pip-24.0:
      Successfully uninstalled pip-24.0
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 3.1/3.1 MB 68.8 MB/s eta 0:00:00


In [2]:
from huggingface_hub import notebook_login

notebook_login()

In [3]:
from datasets import load_dataset

# Load the dataset
dataset = load_dataset("openslr", "SLR66", trust_remote_code = True)

# Set a seed for reproducibility
seed = 42

# Split into 80% training and 20% testing
train_test_split = dataset['train'].train_test_split(test_size=0.1, seed=seed)

# Combine the train and validation into one
train_data = train_test_split['train']  # 80% training
test_data = train_test_split['test']    # 20% testing

# Check sizes
print(f"Training set size: {len(train_data)}")
print(f"Test set size: {len(test_data)}")

openslr.py:   0%|          | 0.00/26.8k [00:00<?, ?B/s]

README.md:   0%|          | 0.00/42.9k [00:00<?, ?B/s]

Generating train split:   0%|          | 0/4448 [00:00<?, ? examples/s]

Training set size: 4003
Test set size: 445


In [4]:
telugu_special_unwanted_characters = [
    'ౄ',  # Vocalic RR
    'ౢ',  # Vocalic L
    'ౣ',  # Vocalic LL
    'ౠ',  # Long Vocalic RR
    'ఽ',  # Avagraha
    '౦', '౧', '౨', '౩', '౪', '౫', '౬', '౭', '౮', '౯',  # Telugu digits
    'ఀ',  # Telugu Sign Combining Candrabindu Above
    'ౘ',  # Letter TTHA
    'ౙ',  # Letter DDA
    'ౚ',  # Letter RHA
    '౷',  # Vedic Tone
    '‘', '’', '“', '”', '%', '.', ';', '-', ',', '/', '\\', '_', '&',  # Common punctuation
    'G', 'P', 'S', 'e', 'l', 'n', 'r', 't', '\u200c' #Unwanted in the dataset
]

In [5]:
import re
chars_to_remove_regex = f'[{re.escape("".join(telugu_special_unwanted_characters))}]'

def remove_special_characters(batch):
    batch["sentence"] = re.sub(chars_to_remove_regex, '', batch["sentence"])
    return batch

In [6]:
train_data = train_data.map(remove_special_characters)
test_data = test_data.map(remove_special_characters)

Map:   0%|          | 0/4003 [00:00<?, ? examples/s]

Map:   0%|          | 0/445 [00:00<?, ? examples/s]

In [7]:
repo_name = "whisper-small-telugu"

In [8]:
from transformers import WhisperFeatureExtractor

feature_extractor = WhisperFeatureExtractor.from_pretrained("openai/whisper-small")

The cache for model files in Transformers v4.22.0 has been updated. Migrating your old cache. This is a one-time only operation. You can interrupt this and resume the migration later on by calling `transformers.utils.move_cache()`.


0it [00:00, ?it/s]

preprocessor_config.json:   0%|          | 0.00/185k [00:00<?, ?B/s]

In [9]:
from transformers import WhisperTokenizer

tokenizer = WhisperTokenizer.from_pretrained("openai/whisper-small", language="Telugu", task="transcribe")

tokenizer_config.json:   0%|          | 0.00/283k [00:00<?, ?B/s]

vocab.json:   0%|          | 0.00/836k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/2.48M [00:00<?, ?B/s]

merges.txt:   0%|          | 0.00/494k [00:00<?, ?B/s]

normalizer.json:   0%|          | 0.00/52.7k [00:00<?, ?B/s]

added_tokens.json:   0%|          | 0.00/34.6k [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/2.19k [00:00<?, ?B/s]

In [10]:
tokenizer.push_to_hub(repo_name)

README.md:   0%|          | 0.00/5.17k [00:00<?, ?B/s]

No files have been modified since last commit. Skipping to prevent empty commit.


CommitInfo(commit_url='https://huggingface.co/kaarthu2003/whisper-small-telugu/commit/5f12dccc3659bbfb762f0e6627ec398cc734ffc1', commit_message='Upload tokenizer', commit_description='', oid='5f12dccc3659bbfb762f0e6627ec398cc734ffc1', pr_url=None, repo_url=RepoUrl('https://huggingface.co/kaarthu2003/whisper-small-telugu', endpoint='https://huggingface.co', repo_type='model', repo_id='kaarthu2003/whisper-small-telugu'), pr_revision=None, pr_num=None)

Ensuring Tokenizer is working correctly

In [11]:
input_str = train_data[0]["sentence"]
labels = tokenizer(input_str).input_ids
decoded_with_special = tokenizer.decode(labels, skip_special_tokens=False)
decoded_str = tokenizer.decode(labels, skip_special_tokens=True)

print(f"Input:                 {input_str}")
print(f"Decoded w/ special:    {decoded_with_special}")
print(f"Decoded w/out special: {decoded_str}")
print(f"Are equal:             {input_str == decoded_str}")

Input:                 సుశర్మ సైన్యాలు వెనుదిరిగాయి
Decoded w/ special:    <|startoftranscript|><|te|><|transcribe|><|notimestamps|>సుశర్మ సైన్యాలు వెనుదిరిగాయి<|endoftext|>
Decoded w/out special: సుశర్మ సైన్యాలు వెనుదిరిగాయి
Are equal:             True


In [12]:
from transformers import WhisperProcessor

processor = WhisperProcessor.from_pretrained("openai/whisper-small", language="Telugu", task="transcribe")

In [13]:
print(train_data[0])

{'path': '/root/.cache/huggingface/datasets/downloads/extracted/b144e57a4462fa4e5ef79b06e911eb4b40a63b7712b29a84bb159f9945f51cbf/tem_03338_00235717313.wav', 'audio': {'path': '/root/.cache/huggingface/datasets/downloads/extracted/b144e57a4462fa4e5ef79b06e911eb4b40a63b7712b29a84bb159f9945f51cbf/tem_03338_00235717313.wav', 'array': array([ 3.05175781e-05,  3.05175781e-05,  6.10351562e-05, ...,
       -3.60107422e-03, -3.57055664e-03, -3.57055664e-03]), 'sampling_rate': 48000}, 'sentence': 'సుశర్మ సైన్యాలు వెనుదిరిగాయి'}


In [14]:
from datasets import Audio

train_data = train_data.cast_column("audio", Audio(sampling_rate=16000))
test_data = test_data.cast_column("audio", Audio(sampling_rate=16000))

In [15]:
print(train_data[0])

{'path': '/root/.cache/huggingface/datasets/downloads/extracted/b144e57a4462fa4e5ef79b06e911eb4b40a63b7712b29a84bb159f9945f51cbf/tem_03338_00235717313.wav', 'audio': {'path': '/root/.cache/huggingface/datasets/downloads/extracted/b144e57a4462fa4e5ef79b06e911eb4b40a63b7712b29a84bb159f9945f51cbf/tem_03338_00235717313.wav', 'array': array([ 2.62748763e-05,  5.04062264e-05,  1.11451918e-05, ...,
       -3.51061067e-03, -3.95959523e-03,  0.00000000e+00]), 'sampling_rate': 16000}, 'sentence': 'సుశర్మ సైన్యాలు వెనుదిరిగాయి'}


In [16]:
def prepare_dataset(batch):
    # load and resample audio data from 48 to 16kHz
    audio = batch["audio"]

    # compute log-Mel input features from input audio array
    batch["input_features"] = feature_extractor(audio["array"], sampling_rate=audio["sampling_rate"]).input_features[0]

    # encode target text to label ids
    batch["labels"] = tokenizer(batch["sentence"]).input_ids
    return batch

In [17]:
train_data = train_data.map(prepare_dataset, remove_columns=train_data.column_names)
test_data = test_data.map(prepare_dataset, remove_columns=test_data.column_names)

Map:   0%|          | 0/4003 [00:00<?, ? examples/s]

Map:   0%|          | 0/445 [00:00<?, ? examples/s]

In [18]:
from transformers import WhisperForConditionalGeneration

model = WhisperForConditionalGeneration.from_pretrained("openai/whisper-small")

config.json:   0%|          | 0.00/1.97k [00:00<?, ?B/s]

model.safetensors:   0%|          | 0.00/967M [00:00<?, ?B/s]

generation_config.json:   0%|          | 0.00/3.87k [00:00<?, ?B/s]

In [19]:
model.generation_config.language = "telugu"
model.generation_config.task = "transcribe"

model.generation_config.forced_decoder_ids = None

In [20]:
import torch

from dataclasses import dataclass
from typing import Any, Dict, List, Union

@dataclass
class DataCollatorSpeechSeq2SeqWithPadding:
    processor: Any
    decoder_start_token_id: int

    def __call__(self, features: List[Dict[str, Union[List[int], torch.Tensor]]]) -> Dict[str, torch.Tensor]:
        # split inputs and labels since they have to be of different lengths and need different padding methods
        # first treat the audio inputs by simply returning torch tensors
        input_features = [{"input_features": feature["input_features"]} for feature in features]
        batch = self.processor.feature_extractor.pad(input_features, return_tensors="pt")

        # get the tokenized label sequences
        label_features = [{"input_ids": feature["labels"]} for feature in features]
        # pad the labels to max length
        labels_batch = self.processor.tokenizer.pad(label_features, return_tensors="pt")

        # replace padding with -100 to ignore loss correctly
        labels = labels_batch["input_ids"].masked_fill(labels_batch.attention_mask.ne(1), -100)

        # if bos token is appended in previous tokenization step,
        # cut bos token here as it's append later anyways
        if (labels[:, 0] == self.decoder_start_token_id).all().cpu().item():
            labels = labels[:, 1:]

        batch["labels"] = labels

        return batch

In [21]:
data_collator = DataCollatorSpeechSeq2SeqWithPadding(
    processor=processor,
    decoder_start_token_id=model.config.decoder_start_token_id,
)

In [22]:
import evaluate

metric = evaluate.load("wer")

In [23]:
def compute_metrics(pred):
    pred_ids = pred.predictions
    label_ids = pred.label_ids

    # replace -100 with the pad_token_id
    label_ids[label_ids == -100] = tokenizer.pad_token_id

    # we do not want to group tokens when computing the metrics
    pred_str = tokenizer.batch_decode(pred_ids, skip_special_tokens=True)
    label_str = tokenizer.batch_decode(label_ids, skip_special_tokens=True)

    wer = metric.compute(predictions=pred_str, references=label_str)

    return {"wer": wer}

In [24]:
import os
os.environ["PYTORCH_CUDA_ALLOC_CONF"] = "expandable_segments:True"

In [25]:
import warnings
import torch

# Suppress warnings
warnings.filterwarnings("ignore", category=FutureWarning)

# Check GPU memory status
print(torch.cuda.memory_summary())

|===========================================================================|
|                  PyTorch CUDA memory summary, device ID 0                 |
|---------------------------------------------------------------------------|
|            CUDA OOMs: 0            |        cudaMalloc retries: 0         |
|===========================================================================|
|        Metric         | Cur Usage  | Peak Usage | Tot Alloc  | Tot Freed  |
|---------------------------------------------------------------------------|
| Allocated memory      |      0 B   |      0 B   |      0 B   |      0 B   |
|       from large pool |      0 B   |      0 B   |      0 B   |      0 B   |
|       from small pool |      0 B   |      0 B   |      0 B   |      0 B   |
|---------------------------------------------------------------------------|
| Active memory         |      0 B   |      0 B   |      0 B   |      0 B   |
|       from large pool |      0 B   |      0 B   |      0 B   |

In [26]:
from transformers import Seq2SeqTrainingArguments

training_args = Seq2SeqTrainingArguments(
    output_dir=repo_name,  # Repository name specific for Telugu
    per_device_train_batch_size=8,  # Adjust if needed for memory constraints
    gradient_accumulation_steps=2,  # Combined batch size is still 16
    learning_rate=1e-5,
    warmup_steps=400,  # Slightly shorter warmup to stabilize learning earlier
    num_train_epochs=10,  # Epoch-based training for stable learning
    gradient_checkpointing=True,
    fp16=True,
    evaluation_strategy="steps",
    per_device_eval_batch_size=8,
    predict_with_generate=True,
    generation_max_length=250,  # Adjusted for longer Telugu transcripts if needed
    save_steps=600,  # Less frequent checkpointing to save space
    eval_steps=200,  # More frequent evaluation for detailed tracking
    logging_steps=400,
    report_to=["tensorboard"],
    load_best_model_at_end=True,
    metric_for_best_model="wer",
    greater_is_better=False,
    push_to_hub=True,
)

In [27]:
from transformers import Seq2SeqTrainer

trainer = Seq2SeqTrainer(
    args=training_args,
    model=model,
    train_dataset=train_data,
    eval_dataset=test_data,
    data_collator=data_collator,
    compute_metrics=compute_metrics,
    tokenizer=processor.feature_extractor,
)


In [28]:
import torch
torch.cuda.empty_cache()

In [29]:
trainer.train()

Passing a tuple of `past_key_values` is deprecated and will be removed in Transformers v4.43.0. You should pass an instance of `EncoderDecoderCache` instead, e.g. `past_key_values=EncoderDecoderCache.from_legacy_cache(past_key_values)`.
`use_cache = True` is incompatible with gradient checkpointing. Setting `use_cache = False`...


You have passed task=transcribe, but also have set `forced_decoder_ids` to [[1, 50259], [2, 50359], [3, 50363]] which creates a conflict. `forced_decoder_ids` will be ignored in favor of task=transcribe.
The attention mask is not set and cannot be inferred from input because pad token is same as eos token. As a consequence, you may observe unexpected behavior. Please pass your input's `attention_mask` to obtain reliable results.
/opt/conda/lib/python3.10/site-packages/transformers/modeling_utils.py:2618: UserWarning: Moving the following attributes in the config to the generation config: {'max_length': 448, 'suppress_tokens': [1, 2, 7, 8, 9, 10, 14, 25, 26, 27, 28, 29, 31, 58, 59, 60, 61, 62, 63, 90, 91, 92, 93, 359, 503, 522, 542, 873, 893, 902, 918, 922, 931, 1350, 1853, 1982, 2460, 2627, 3246, 3253, 3268, 3536, 3846, 3961, 4183, 4667, 6585, 6647, 7273, 9061, 9383, 10428, 10929, 11938, 12033, 12331, 12562, 13793, 14157, 14635, 15265, 15618, 16553, 16604, 18362, 18956, 20075, 21675, 2

TrainOutput(global_step=2500, training_loss=0.10525472162216902, metrics={'train_runtime': 23141.0009, 'train_samples_per_second': 1.73, 'train_steps_per_second': 0.108, 'total_flos': 1.15304296697856e+19, 'train_loss': 0.10525472162216902, 'epoch': 9.980039920159681})

In [30]:
trainer.push_to_hub()

CommitInfo(commit_url='https://huggingface.co/kaarthu2003/whisper-small-telugu/commit/d2c0ef3de41d51fbc11a08aa0286857106b74895', commit_message='End of training', commit_description='', oid='d2c0ef3de41d51fbc11a08aa0286857106b74895', pr_url=None, repo_url=RepoUrl('https://huggingface.co/kaarthu2003/whisper-small-telugu', endpoint='https://huggingface.co', repo_type='model', repo_id='kaarthu2003/whisper-small-telugu'), pr_revision=None, pr_num=None)

In [31]:
from transformers import WhisperForConditionalGeneration, WhisperProcessor

model = WhisperForConditionalGeneration.from_pretrained("kaarthu2003/whisper-small-telugu")
processor = WhisperProcessor.from_pretrained("kaarthu2003/whisper-small-telugu")

config.json:   0%|          | 0.00/1.38k [00:00<?, ?B/s]

model.safetensors:   0%|          | 0.00/967M [00:00<?, ?B/s]

generation_config.json:   0%|          | 0.00/3.79k [00:00<?, ?B/s]

preprocessor_config.json:   0%|          | 0.00/339 [00:00<?, ?B/s]

tokenizer_config.json:   0%|          | 0.00/283k [00:00<?, ?B/s]

vocab.json:   0%|          | 0.00/1.04M [00:00<?, ?B/s]

merges.txt:   0%|          | 0.00/494k [00:00<?, ?B/s]

normalizer.json:   0%|          | 0.00/52.7k [00:00<?, ?B/s]

added_tokens.json:   0%|          | 0.00/34.6k [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/2.19k [00:00<?, ?B/s]

In [40]:
print(test_data[0])

{'input_features': [[-0.5372480154037476, -0.5410044193267822, -0.5703588724136353, -0.33495354652404785, -0.086478590965271, -0.03678107261657715, -0.09879207611083984, -0.4234638214111328, -0.4856482744216919, -0.49749720096588135, -0.5014975070953369, -0.3318183422088623, -0.28250205516815186, -0.3377887010574341, -0.40973615646362305, -0.5961219072341919, -0.7352572679519653, -0.49948930740356445, -0.3668147325515747, -0.4123159646987915, -0.2344357967376709, -0.14456188678741455, -0.1138303279876709, -0.11190569400787354, -0.06739938259124756, -0.02708280086517334, -0.13588380813598633, -0.3529726266860962, -0.30972790718078613, -0.2739025354385376, -0.550926923751831, -0.37614405155181885, -0.35150980949401855, -0.5114895105361938, -0.6277055740356445, -0.5365887880325317, -0.5388915538787842, -0.3141120672225952, -0.3329547643661499, -0.3265882730484009, -0.2238938808441162, -0.21496856212615967, -0.2678591012954712, -0.3448740243911743, -0.4338463544845581, -0.4246574640274048,

In [53]:
import torch

device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
model.to(device)

# Placeholder to store predictions and references
predictions = []
references = []

# Evaluate your model on the test data
for example in test_data:
    # Extract input features and labels
    input_features = example["input_features"]
    label = example["labels"]

    # Move input features to device
    input_features = torch.tensor(input_features).unsqueeze(0).to(device)

    # Generate predictions
    predicted_ids = model.generate(input_features)
    predicted_text = processor.batch_decode(predicted_ids, skip_special_tokens=True)[0]

    # Check if label is an integer or needs formatting
    if isinstance(label, int):
        label = [label]  # Wrap the single integer in a list if necessary

    # Decode the label to get the reference text
    reference_text = processor.batch_decode([label], skip_special_tokens=True)[0]

    # Append to lists
    predictions.append(predicted_text)
    references.append(reference_text)

# Compute WER
wer = metric.compute(predictions=predictions, references=references)
print(f"Word Error Rate (WER): {wer:.2f}")
cer_metric = evaluate.load("cer")
cer = cer_metric.compute(predictions=predictions, references=references)
print(f"Character Error Rate (CER): {cer: .2f}")

Word Error Rate (WER): 0.28


Character Error Rate (CER):  0.05
